In [1]:
!pip install --user nglview #Устанавливаем все необходимое

/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


In [2]:
import nglview as nv #Импортируем все необходимое
import requests
import json 

In [3]:
my_query = {   #Шаблон запроса
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}

In [4]:
keyword_clause = {   #Ключевые слова: streptomycin
    "type": "terminal",
    "service": "full_text",
    "parameters": {
        "value": "streptomycin"
    }
}

my_query["query"]["nodes"].append(keyword_clause)

In [5]:
resolution_clause = {   #Разрешение: не хуже 2.3 ангстрем
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.3,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

In [6]:
has_ligand_clause = {   #Количество лигандов: не менее 3
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 2,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

In [7]:
date_range_clause = {   #Дата: 2015-01-01 - 2020-01-01
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2015-01-01",
            "to": "2020-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

In [8]:
rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'  #Отправляем запрос на сайт
json_query = json.dumps(my_query) #превращаем запрос в строку
search = requests.post(f'{rcsb}', data=json_query) #отправляем по адресу

In [9]:
search  #Все прошло правильно

<Response [200]>

In [10]:
search_result = search.json()

In [11]:
best_hit = search_result["result_set"][0]  #Лучший результат - PDB ID 5LUH, первый в result_set
best_hit

{'identifier': '5LUH',
 'score': 0.9932105682811432,
 'services': [{'service_type': 'full_text',
   'nodes': [{'node_id': 8262,
     'original_score': 16.526094436645508,
     'norm_score': 0.9728422731245727}]},
  {'service_type': 'text',
   'nodes': [{'node_id': 7609, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 7020, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 6914, 'original_score': 1.0, 'norm_score': 1.0}]}]}

In [12]:
view = nv.show_pdbid('5luh') 
view

NGLWidget()

In [13]:
from ipywidgets import interact, fixed

In [14]:
representations = [   #Список типов отображения
  'ball+stick',      
  'backbone',        
  'cartoon',         
  'helixorient',   
  'hyperball',       
  'licorice',        
  'line',            
  'point',          
  'ribbon',          
  'rocket',       
  'rope',          
  'spacefill',     
  'surface',    
  'trace',           
  'tube'             
]

In [15]:
colors = [   #Список цветовых схем
  'random',
  'uniform',
  'atomindex',
  'residueindex',
  'chainindex',
  'sstruc',
  'element',
  'resname',
  'bfactor',
  'hydrophobicity',
]

In [16]:
my_examples = {   #3 варианта отображения
    'Example 1': {
        'description': '''
Вариант 1.
Поверхность белка покрашена в белый, с непрозрачностью 0.1
Белок в виде rope красного цвета
Боковые радикалы в стержневой модели, покрашенные согласно элементу
Лиганды в виде Ван-дер-Ваальсовых сфер, покрашены по элементам
''',
        'representations': [
            {
                'type': 'surface',                      
                'params': {
                    'sele': 'protein',              
                    'color': 'white',
                    'opacity': 0.1                    
                 }
            },
            {
                'type': 'rope',
                'params': {
                    'sele': 'protein',                 
                    'color': 'red'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                
                    'color': 'element'  
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ligand',               
                    'color': 'element'  
                 }
            },
        ],
    },
    'Example 2': {
        'description': '''
Вариант 4.
Белок в виде cartoon, покраска по типу вторичной структуры
Боковые радикалы покрашены по элементу, показаны линиями
Боковые радикалы ароматических аминокислот показаны в стержневой модели
Лиганды показаны в виде Ван-дер-Ваальсовых сфер, покрашены по гидрофобности
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'sstruc'  
                 }
            },
            {
                'type': 'line',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached and aromatic',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'spacefill',                      
                'params': {
                    'sele': 'ligand',                     
                    'color': 'hydrophobicity'  
                 }
            },                
        ],
    },
    'Example 3': {
        'description': '''
Вариант 9.
Остов белка в шаростержневой модели, покрашен по элементам
Боковые радикалы в стержневой модели, покрашены по элементам
Углероды остатков с 30 по 70-й покрашены в светло-голубой
Лиганды показаны в виде линий, покрашены в любой оттенок оранжевого
''',
        'representations': [
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'protein and backbone',               
                    'color': 'element'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'protein and sidechainAttached',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'protein and 30-70 and _C',                     
                    'color': 'lightblue'  
                 }
            },
            {
                'type': 'line',
                'params': {
                    'sele': 'ligand',                     
                    'color': '#FF8B00'  
                 }
            },
        ],
    },
}

In [17]:
def show_examples(view, example_name):   #Код для интерактивной ячейки с 3 вариантами отображения
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("5luh", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Example 1', 'Example 2', 'Example 3'), va…

NGLWidget()